# libraries

In [14]:
import requests
from bs4 import BeautifulSoup
import math
import re
from datetime import datetime
import locale
from cryptography.fernet import Fernet
import json
import tempfile
import pysftp
import os
import psycopg2
from dotenv import load_dotenv


headers = {
            'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/116.0.0.0 Safari/537.36'
        }
pattern = re.compile(r'\d+')

C:\Users\Lenovo\AppData\Local\Temp\ipykernel_1928\1353659066.py:15 DeprecationWarning: The `airflow.hooks.postgres_hook.PostgresHook` class is deprecated. Please use `'airflow.providers.postgres.hooks.postgres.PostgresHook'`.

ImportError: Could not import `airflow.providers.postgres.hooks.postgres.PostgresHook` while trying to import `airflow.hooks.postgres_hook.PostgresHook`.

# Load virtual environment passwords.

In [7]:
#teste 1
load_dotenv()


True

# Transform password into bytes

In [8]:
key_bytes = os.getenv('chave').encode('utf-8')

# Cryptography functions and database inputs

In [26]:
def extract_page_number(soup):
    url = f"{soup}"
    pages = requests.get(url, headers=headers)
    soup_content = BeautifulSoup(pages.content, 'html.parser')
    
    pagination = soup_content.find('ul', class_='pagination pagination-lg')
    span = pagination.find_all('span')
    print(span)
    itens_number_text = span[2].text
    transform_itens_number = itens_number_text.replace(".", "")

    try:
        list_of_integer_number = re.findall(pattern, transform_itens_number)
    except ValueError:
        print("Error to convert itens to integer.")
        return None
    number_of_itens = int(list_of_integer_number[2])
    result = number_of_itens / 25
    last_page = math.ceil(result)
    return last_page

# Functions to encrypt data
def encryption(name):
    cipher_suite = Fernet(key_bytes)
    print(cipher_suite)
    encrypted_text = cipher_suite.encrypt(json.dumps(name, ensure_ascii=False).encode('utf-8'))
    return encrypted_text

# Functions to decryption and loading
def decryption_and_loading(encrypted_text,table,master_key):
    
    # SFTP Connection Settings
    host = Variable.get('host')
    username = Variable.get('username')
    port = 22
    password = Variable.get('password')
    cnopts = pysftp.CnOpts()
    cnopts.hostkeys = None  # Disable hostkey verification
    
    # Temp file
    with tempfile.NamedTemporaryFile(delete=False, suffix='.txt') as temp_file:
        temp_filename = temp_file.name
        temp_file.write(encrypted_text)
        temp_file.seek(0)
        temp_file.close()
    
    
        with pysftp.Connection(host, username=username, password=password, port=port, cnopts=cnopts) as sftp:
            remote_path_upload = f"C:\\Users\\Lenovo\\Desktop\\Projeto Data WH\\data output\\{table}.txt"
            sftp.put(temp_filename, remote_path_upload)
            
            os.remove(temp_filename)
        
            # Download a file from the SFTP server
            remote_path_download = f"C:\\Users\\Lenovo\\Desktop\\Projeto Data WH\\data output\\{table}.txt"
            local_path_download = 'remote_file_path_to_download.txt'
            sftp.get(remote_path_download, local_path_download)
            
    
    # Decrypt encrypted file data
    with open(local_path_download, 'rb') as encrypted_file:
        encrypted_date = encrypted_file.read().decode('utf-8') 
        cipher_suite = Fernet(key_bytes)      
        decrypt_text = cipher_suite.decrypt(encrypted_date)
        decrypt_date = decrypt_text.decode('utf-8')
        decrypt_dictionary = json.loads(decrypt_date)
        
    keys = []
    values = []
    
    for dictionary in decrypt_dictionary:
        for key, value in dictionary.items():
            keys.append(key)
            values.append(value)

    # # Substitua 'my_conn_id' pelo ID da sua conexão definida no Airflow
    # conexao_id = 'postgres-airflow'

    # # Obtenha a conexão do Airflow para o banco de dados
    # conexao = BaseHook.get_connection(conexao_id)
   
    # db_config = {
    #     'host': 'localhost',
    #     'database': conexao.Database,
    #     'user': conexao.Login,
    #     'password': conexao.Password
        
    # }
    db_config = {
        'conn_id': 'postgres-airflow',  # Use o Conn Id configurado no Airflow
    }
    
    # Create a connection to the PostgreSQL database
    try:
        connection = PostgresHook(postgres_conn_id=db_config['conn_id']).get_conn()
        cursor = connection.cursor()
    
        
        # Query the database for existing keys 
        sql_query = f"SELECT {master_key} FROM {table};"
        
        # Execute the SQL query
        cursor.execute(sql_query)
        date_of_database = cursor.fetchall()
        
        # Run SQL query to get the unique keys that exist in the database
        desired_key = f'{master_key}'
        
        existing_keys = [value1 for tupla in date_of_database for value1 in tupla]
        existing_keys = set(existing_keys)
        

        new_keys = {dictionary[desired_key] for dictionary in decrypt_dictionary}
        new_keys = {int(number) for number in new_keys}
        print(new_keys)
        # Import only keys that do not already exist in the database
        keys_new = new_keys - existing_keys
        keys_new = list(keys_new)
        print(keys_new)
        
        data_to_insert = []

        for dictionary in decrypt_dictionary:
            # Checks if the desired key is present in the dictionary
            if int(dictionary[desired_key]) in keys_new:
                # Add the complete dictionary to the list
                data_to_insert.append(dictionary)
        print(data_to_insert)
                
                
        try:
            for dictionary_insert in data_to_insert:
                sql_query = f"INSERT INTO {table} ({', '.join(dictionary_insert.keys())}) VALUES ({', '.join(['%s' for _ in dictionary_insert.values()])})"
                
                tupla_values = tuple(dictionary_insert.values())

                # Execute the SQL query
                cursor.execute(sql_query,tupla_values)

                # Commit to confirm the transaction
                connection.commit()
                print("Successful insertion.") 
        except Exception as e:
            print("Error executing SQL query:", e)
                
    except Exception as e:
        print("Error executing SQL query:", e)
        
        
    finally:
        # Close the database connection
        if connection:
            cursor.close()
            connection.close()
    
    return 
     

In [18]:
# Criar uma sessão Spark
spark =SparkSession.builder.appName("ColetaParalela").getOrCreate()

# Lista de Urls para coletar
urls=[]
for number_page in range(1, 380 + 1):
        
        urls.append(f"https://www.cbf.com.br/futebol-brasileiro/atletas/campeonato-brasileiro-serie-a/2023?atleta=&page={number_page}&csrt=5141281007868528954")

rdd_urls = spark.sparkContext.parallelize(urls, numSlices=10)

def extract_players_informations_cbf(url):
        try:
                headers = {
                        'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/116.0.0.0 Safari/537.36'}
        
                site = requests.get(url, headers=headers)
                soup = BeautifulSoup(site.content, "html.parser")
                body = soup.find('tbody')
                lines = body.find_all('tr')
                
                players_informations = []

                for line in lines:
                        columns = line.find_all('a')
                        name_columns = columns[0]
                        link = name_columns['href']
                        id_player = re.findall(pattern, link)
                        img = line.find('img')
                        title = "title nor found" if img is None else img['alt']
                        
                        players_informations.append({
                        'id_players': id_player[0],
                        'name': columns[0].text.strip(),
                        'nickname': columns[1].text.strip(),
                        'team': title,
                        'year':id_player[1]
                        })

        except Exception as e:
            print(f"Error on page {number_page}: {str(e)}")

        return players_informations

#coleta paralela de dados
dados_coletados = rdd_urls.map(lambda url: extract_players_informations_cbf(url)).collect()

#finalizar a sessão spark
spark.stop()

Py4JJavaError: An error occurred while calling z:org.apache.spark.api.python.PythonRDD.collectAndServe.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 2 in stage 6.0 failed 1 times, most recent failure: Lost task 2.0 in stage 6.0 (TID 31) (host.docker.internal executor driver): org.apache.spark.SparkException: Python worker failed to connect back.
	at org.apache.spark.api.python.PythonWorkerFactory.createSimpleWorker(PythonWorkerFactory.scala:203)
	at org.apache.spark.api.python.PythonWorkerFactory.create(PythonWorkerFactory.scala:109)
	at org.apache.spark.SparkEnv.createPythonWorker(SparkEnv.scala:124)
	at org.apache.spark.api.python.BasePythonRunner.compute(PythonRunner.scala:174)
	at org.apache.spark.api.python.PythonRDD.compute(PythonRDD.scala:67)
	at org.apache.spark.rdd.RDD.computeOrReadCheckpoint(RDD.scala:364)
	at org.apache.spark.rdd.RDD.iterator(RDD.scala:328)
	at org.apache.spark.scheduler.ResultTask.runTask(ResultTask.scala:93)
	at org.ap

# players_information

In [61]:
last_page = extract_page_number("https://www.cbf.com.br/futebol-brasileiro/atletas/campeonato-brasileiro-serie-a/2023?atleta=&page=1&csrt=3199419627270262597")
 

def extract_players_informations_cbf(pages):
    players_informations = []

    for number_page in range(1, pages + 1):
        url = f"https://www.cbf.com.br/futebol-brasileiro/atletas/campeonato-brasileiro-serie-a/2023?atleta=&page={number_page}&csrt=5141281007868528954"
        headers = {
            'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/116.0.0.0 Safari/537.36'
        }
        
        try:
            site = requests.get(url, headers=headers)
            soup = BeautifulSoup(site.content, "html.parser")
            body = soup.find('tbody')
            lines = body.find_all('tr')

            for line in lines:
                columns = line.find_all('a')
                name_columns = columns[0]
                link = name_columns['href']
                id_player = re.findall(pattern, link)
                img = line.find('img')
                title = "title nor found" if img is None else img['alt']
                
                players_informations.append({
                    'id_players': id_player[0],
                    'name': columns[0].text.strip(),
                    'nickname': columns[1].text.strip(),
                    'team': title,
                    'year':id_player[1]
                })

        except Exception as e:
            print(f"Error on page {number_page}: {str(e)}")

    return players_informations

players_informations = extract_players_informations_cbf(last_page)


[<span>« Anterior</span>, <span>Próximo »</span>, <span>
        1 a 25 | total 1.061      </span>]


# Transform and Load
## Encriptify/descriptify and input players information

In [81]:
players_informations_encriptify = encryption(players_informations)

players_informations_descriptify_and_input = decryption_and_loading(players_informations_encriptify,'relational.players_informations','id_players')

# team_informations

In [5]:
def extract_teams_informations_cbf():
    teams_informations = []
    try:
        url_team = "https://www.cbf.com.br/futebol-brasileiro/times/campeonato-brasileiro-serie-a/2023"
        site = requests.get(url_team, headers=headers)
        soup_times = BeautifulSoup(site.content, "html.parser")
        row = soup_times.find_all('div',class_='col-md-3 p-10')
        
        for time in row:
            a = time.find('a')
            link = a['href']
            img = a.find('img')
            name = img['alt']
            team_reference = re.findall(pattern, link)
            
            if name != 'Esporte Clube Bahia - BA' and name != 'Atlético Mineiro - MG':
                teams_informations.append({
                'id_team': team_reference[1],
                'name': name,
                'year':team_reference[0]
                })
    except Exception as e:
        print(f"Error on page: {str(e)}")
    return teams_informations

teams_informations = extract_teams_informations_cbf()

print(teams_informations)

[{'id_team': '59897', 'name': 'América Saf - MG', 'year': '2023'}, {'id_team': '20052', 'name': 'Athletico Paranaense - PR', 'year': '2023'}, {'id_team': '62194', 'name': 'Atlético Mineiro Saf - MG', 'year': '2023'}, {'id_team': '61377', 'name': 'Bahia - BA', 'year': '2023'}, {'id_team': '60175', 'name': 'Botafogo - RJ', 'year': '2023'}, {'id_team': '20001', 'name': 'Corinthians - SP', 'year': '2023'}, {'id_team': '61590', 'name': 'Coritiba S.a.f. - PR', 'year': '2023'}, {'id_team': '59849', 'name': 'Cruzeiro Saf - MG', 'year': '2023'}, {'id_team': '20800', 'name': 'Cuiabá Saf - MT', 'year': '2023'}, {'id_team': '20016', 'name': 'Flamengo - RJ', 'year': '2023'}, {'id_team': '20014', 'name': 'Fluminense - RJ', 'year': '2023'}, {'id_team': '20048', 'name': 'Fortaleza - CE', 'year': '2023'}, {'id_team': '20028', 'name': 'Goiás - GO', 'year': '2023'}, {'id_team': '20013', 'name': 'Grêmio - RS', 'year': '2023'}, {'id_team': '20011', 'name': 'Internacional - RS', 'year': '2023'}, {'id_team':

# Transform and Load
## Encriptify/descriptify and input teams information

In [6]:
teams_informations_encriptify = encryption(teams_informations)

teams_informations_descriptify_and_input = decryption_and_loading(teams_informations_encriptify,'relational.teams_informations','id_team')

[{'id_team': '59897', 'name': 'América Saf - MG', 'year': '2023'}, {'id_team': '20052', 'name': 'Athletico Paranaense - PR', 'year': '2023'}, {'id_team': '62194', 'name': 'Atlético Mineiro Saf - MG', 'year': '2023'}, {'id_team': '61377', 'name': 'Bahia - BA', 'year': '2023'}, {'id_team': '60175', 'name': 'Botafogo - RJ', 'year': '2023'}, {'id_team': '20001', 'name': 'Corinthians - SP', 'year': '2023'}, {'id_team': '61590', 'name': 'Coritiba S.a.f. - PR', 'year': '2023'}, {'id_team': '59849', 'name': 'Cruzeiro Saf - MG', 'year': '2023'}, {'id_team': '20800', 'name': 'Cuiabá Saf - MT', 'year': '2023'}, {'id_team': '20016', 'name': 'Flamengo - RJ', 'year': '2023'}, {'id_team': '20014', 'name': 'Fluminense - RJ', 'year': '2023'}, {'id_team': '20048', 'name': 'Fortaleza - CE', 'year': '2023'}, {'id_team': '20028', 'name': 'Goiás - GO', 'year': '2023'}, {'id_team': '20013', 'name': 'Grêmio - RS', 'year': '2023'}, {'id_team': '20011', 'name': 'Internacional - RS', 'year': '2023'}, {'id_team':

# referees_informations

In [ ]:
last_page = extract_page_number("https://www.cbf.com.br/a-cbf/arbitragem/relacao-arbitros")


def extract_referees_informations_cbf(pages):
    referees_informations = []

    for number_page in range(1, pages + 1):
        url = f"https://www.cbf.com.br/a-cbf/arbitragem/relacao-arbitros?p=&l=&f=0&c=0&j=0&page={number_page}"
        headers = {
            'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/116.0.0.0 Safari/537.36'
        }
        
        try:
            site = requests.get(url, headers=headers)
            soup = BeautifulSoup(site.content, "html.parser")
            body = soup.find('tbody')
            lines = body.find_all('tr')

            for line in lines:
                columns = line.find_all('td')
                columns_name = columns[0]
                a = columns_name.find('a')
                link = a['href']
                id_referees = re.findall(pattern, link)
                name = columns[0].find('b')
                function = columns[1]
                federation = columns[2]
                
                referees_informations.append({
                    'id_referees': id_referees[0],
                    'name': name.text.strip(),
                    'function': function.text.strip(),
                    'federation': federation.text.strip()
                })

        except Exception as e:
            print(f"Error on page {number_page}: {str(e)}")

    return referees_informations


referees_informations = extract_referees_informations_cbf(last_page)
for info in referees_informations:
    print(info)

# Transform and Load
## Encriptify/descriptify and input referees information

In [ ]:
referees_informations_encriptify = encryption(referees_informations)

referees_informations_descriptify_input = decryption_and_loading(referees_informations_encriptify,'relational.referees_informations','id_referees')

# referees statistics

In [14]:
def extract_referees_statistics_cbf(pages):
    referees_statistics = []
    id_referees_statistics = 0
    for number_page in range(1, pages + 1):
        url = f"https://www.cbf.com.br/futebol-brasileiro/competicoes/campeonato-brasileiro-serie-a/2023/{number_page}"
        headers = {
            'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/116.0.0.0 Safari/537.36'
        }    
        try:
            site = requests.get(url, headers=headers)
            soup = BeautifulSoup(site.content, "html.parser")
            body = soup.find('tbody')
            lines = body.find_all('tr')
            

            for line in lines:
                a = line.find('a')
                link = a['href']
                id_referees = re.findall(pattern,link)
                functions = line.find('th')
                columns = line.find_all('td')
                name = columns[0]            
                federation = columns[1]
                id_referees_statistics +=1 
                
                
                referees_statistics.append({
                    'id_referees_statistics': id_referees_statistics,
                    'id_match': number_page,
                    'id_referees': id_referees,
                    'functions': functions.text.strip(),
                    'name': name.text.strip(),
                    'federation': federation.text.strip()
                })
                print(referees_statistics)
        except Exception as e:
            print(f"Error on page {number_page}: {str(e)}")

    return referees_statistics


referees_statistics = extract_referees_statistics_cbf(380)
print(referees_statistics)


[{'idEstatistica_arbitros': 1, 'Idjogo': 1, 'IdArbitro': ['16458'], 'Função': 'Árbitro', 'Nome': 'Rodrigo Jose Pereira de Lima', 'Federação': 'PE'}]
[{'idEstatistica_arbitros': 1, 'Idjogo': 1, 'IdArbitro': ['16458'], 'Função': 'Árbitro', 'Nome': 'Rodrigo Jose Pereira de Lima', 'Federação': 'PE'}, {'idEstatistica_arbitros': 2, 'Idjogo': 1, 'IdArbitro': ['703'], 'Função': 'Árbitro Assistente 1', 'Nome': 'Danilo Ricardo Simon Manis\r\n                                      (FIFA)', 'Federação': 'SP'}]
[{'idEstatistica_arbitros': 1, 'Idjogo': 1, 'IdArbitro': ['16458'], 'Função': 'Árbitro', 'Nome': 'Rodrigo Jose Pereira de Lima', 'Federação': 'PE'}, {'idEstatistica_arbitros': 2, 'Idjogo': 1, 'IdArbitro': ['703'], 'Função': 'Árbitro Assistente 1', 'Nome': 'Danilo Ricardo Simon Manis\r\n                                      (FIFA)', 'Federação': 'SP'}, {'idEstatistica_arbitros': 3, 'Idjogo': 1, 'IdArbitro': ['2350'], 'Função': 'Árbitro Assistente 2', 'Nome': 'Karla Renata Cavalcanti de Santana

In [13]:
print(referees_statistics)

NameError: name 'referees_statistics' is not defined

# Transform and Load
## Encriptify/descriptify and input referees statistic

In [12]:
referees_statistics_encriptify = encryption(referees_statistics)

# referees_statistics_descriptify_and_input = decryption_and_loading(referees_statistics_encriptify,'relational.referees_statistics','id_match')

NameError: name 'referees_statistics' is not defined

# players statistics

In [5]:
 def extract_players_statistics_cbf():
    players_statistics = []
    id_players_statistics = 0
    list_player = []
    for number_page in range(1, 380+1):
        url = f"https://www.cbf.com.br/futebol-brasileiro/competicoes/campeonato-brasileiro-serie-a/2023/{number_page}#escalacao"
        headers = {
            'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/116.0.0.0 Safari/537.36'
        }
        try:
            site = requests.get(url, headers=headers)
            soup = BeautifulSoup(site.content, "html.parser")
            lineup = soup.find(
                'div', class_='col-xs-12 col-sm-8 col-md-8 col-lg-8')
            columns = lineup.find_all(
                'ul', class_=re.compile(r'\blist list-unstyled\b'))

            for index_column, column in enumerate(columns):
                if column.find("li", string="Lineup not released"):
                    continue
                line_li = column.find_all('li')

                if line_li:
                    for li in line_li:
                        role = 'Starting' if index_column < 2 else 'Reserve'
                        players = li.find('a')
                        if players:
                            players = players.text.strip() 
                        icon = li.find_all('i')
                        goal = 0
                        own_goal = 0
                        yellow_card = 0
                        red_card = 0
                        time = []
                        minutes = []
                        id_players_statistics += 1
                         
                        for i in icon:
                            classes_i = i.get('class')

                            if 'small' in classes_i and 'icon' in classes_i and 'icon-yellow-card' not in classes_i:
                                goal += 1
                                if 'title' in i.attrs:
                                    time_of_match = i['title']
                                    list_time_of_match = re.findall(
                                        pattern, time_of_match)

                                    if list_time_of_match:
                                        if len(list_time_of_match) == 3:
                                            time_val = int(
                                                list_time_of_match[2])
                                            minutes_val = int(
                                                list_time_of_match[0]) + int(list_time_of_match[1])

                                        else:
                                            time_val = int(
                                                list_time_of_match[1])
                                            minutes_val = int(
                                                list_time_of_match[0])
                                        time.append(time_val)
                                        minutes.append(minutes_val)
                            if 'small' in classes_i and 'icon' in classes_i and 'icon-yellow-card' in classes_i:
                                yellow_card += 1
                            if 'small' in classes_i and 'icon' in classes_i and 'icon-red-card' in classes_i:
                                red_card += 1
                        div_list_phrese = soup.find(
                            'div', class_="col-xs-3 col-sm-3 text-left hidden-xs")
                        list_phrase = div_list_phrese.find_all(
                            'p', class_='time-jogador color-red')
                        if list_phrase:
                            for list_ in list_phrase:
                                list_player_name_match = re.match(
                                    r'\w+', list_.text.strip())
                                if list_player_name_match:
                                    list_player_name = list_player_name_match.group()
                                    list_player_name_split = list_player_name.split()
                                    #aqui ja estou com a lista de pessoas com gol contra
                                    for player_name in list_player_name_split:
                                        list_player.append(players)
                                        for players1 in list_player:
                                            if players1 == player_name:
                                                own_goal = 1
                                            else:
                                                own_goal = 0
                                else:
                                    list_player_name = None
                        goal -= own_goal
                        players_statistics.append({
                            'id_players_statistic': id_players_statistics,
                            'id_match': number_page,
                            'id_players': players,
                            'role': role,
                            'goal': goal,
                            'own_goal': own_goal,
                            'time': time,
                            'minutes': minutes,
                            'yellow_card': yellow_card,
                            'red_card': red_card
                        })
                else:
                    print(
                        "No players were found in the column. Continuing in the next column....")
        except Exception as e:
            print(f"Error on page {number_page}: {str(e)}")
    return players_statistics

players_statistics = extract_players_statistics_cbf()

for info in players_statistics:
    print(info)

{'id_players_statistic': 1, 'id_match': 1, 'id_players': 'Santos', 'role': 'Starting', 'goal': 0, 'own_goal': 0, 'time': [], 'minutes': [], 'yellow_card': 0, 'red_card': 0}
{'id_players_statistic': 2, 'id_match': 1, 'id_players': 'Ayrton Lucas', 'role': 'Starting', 'goal': 1, 'own_goal': 0, 'time': [1], 'minutes': [11], 'yellow_card': 0, 'red_card': 0}
{'id_players_statistic': 3, 'id_match': 1, 'id_players': 'Everton', 'role': 'Starting', 'goal': 0, 'own_goal': 0, 'time': [], 'minutes': [], 'yellow_card': 0, 'red_card': 0}
{'id_players_statistic': 4, 'id_match': 1, 'id_players': 'Bruno Henrique', 'role': 'Starting', 'goal': 0, 'own_goal': 0, 'time': [], 'minutes': [], 'yellow_card': 0, 'red_card': 0}
{'id_players_statistic': 5, 'id_match': 1, 'id_players': 'Gerson', 'role': 'Starting', 'goal': 0, 'own_goal': 0, 'time': [], 'minutes': [], 'yellow_card': 0, 'red_card': 0}
{'id_players_statistic': 6, 'id_match': 1, 'id_players': 'Leo Pereira', 'role': 'Starting', 'goal': 0, 'own_goal': 0,

# Transform and Load
## Encriptify/descriptify and input players statistic

In [29]:
players_statistics_encriptify = encryption(players_statistics)

players_statistics_descriptify_and_input = decryption_and_loading(players_statistics_encriptify,'relational.players_statistics','id_match')


{1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 220, 221, 22

In [27]:
print(players_statistics_descriptify_and_input)

[{'id_players_statistic': 1, 'id_match': 1, 'id_players': 'Santos', 'role': 'Starting', 'goal': 0, 'own_goal': 0, 'time': [], 'minutes': [], 'yellow_card': 0, 'red_card': 0}, {'id_players_statistic': 2, 'id_match': 1, 'id_players': 'Ayrton Lucas', 'role': 'Starting', 'goal': 1, 'own_goal': 0, 'time': [1], 'minutes': [11], 'yellow_card': 0, 'red_card': 0}, {'id_players_statistic': 3, 'id_match': 1, 'id_players': 'Everton', 'role': 'Starting', 'goal': 0, 'own_goal': 0, 'time': [], 'minutes': [], 'yellow_card': 0, 'red_card': 0}, {'id_players_statistic': 4, 'id_match': 1, 'id_players': 'Bruno Henrique', 'role': 'Starting', 'goal': 0, 'own_goal': 0, 'time': [], 'minutes': [], 'yellow_card': 0, 'red_card': 0}, {'id_players_statistic': 5, 'id_match': 1, 'id_players': 'Gerson', 'role': 'Starting', 'goal': 0, 'own_goal': 0, 'time': [], 'minutes': [], 'yellow_card': 0, 'red_card': 0}, {'id_players_statistic': 6, 'id_match': 1, 'id_players': 'Leo Pereira', 'role': 'Starting', 'goal': 0, 'own_goa

In [16]:
def extract_match_results_cbf(pages):
    match_results = []
    id_match_results = 0

    for number_page in range(1, pages + 1):
        url = f"https://www.cbf.com.br/futebol-brasileiro/competicoes/campeonato-brasileiro-serie-a/2023/{number_page}#escalacao"
        headers = {
            'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/116.0.0.0 Safari/537.36'
        }  
        try:
            site = requests.get(url, headers=headers)
            soup = BeautifulSoup(site.content, "html.parser")
            match_data = soup.find('div', class_='col-sm-8')
            match_data_elements = match_data.find_all('span', class_ ="text-2 p-r-20" )
            scoreboard = soup.find('div', class_='placar-wrapper')
            strong = scoreboard.find_all('strong', class_='time-gols block')
            
            # Lista para armazenar os gols das duas equipes
            teams_goals = [int(team.text.strip()) for team in strong]
            
            
            for i, teams in enumerate(strong):
                team = i+1
                if i == 0:
                    id_match_results = (number_page*2)-1
                elif i == 1:
                    id_match_results = (number_page*2)
                # Nome
                name = scoreboard.find('h3', class_='time-nome color-white').text.strip()
                
                # Pontos inicializados como 0
                score = 0
                
                # Lógica para atribuir pontos com base na quantidade de gols
                if teams_goals[0] > teams_goals[1]:
                    score = 3 if i == 0 else 0
                elif teams_goals[0] < teams_goals[1]:
                    score = 3 if i == 1 else 0
                else:
                    score = 1

                for index_elements, elements in enumerate(match_data_elements):
                    if index_elements == 0:
                        local = elements.text.strip()
                    elif index_elements == 1:
                        date_complete = elements.text.strip()
                        match = re.search(r',(.*)', date_complete)
                        date_original = match.group(1).strip()
                        locale.setlocale(locale.LC_TIME, 'pt_BR.UTF-8')
                        date_obj = datetime.strptime(date_original, "%d de %B de %Y")
                        date = date_obj.strftime("%d/%m/%Y")
            
                match_results.append({
                    'id_match_result': id_match_results,
                    'id_match': number_page,
                    'local': local,
                    'date': date,
                    'team': team,
                    'name': name,
                    'goal': teams_goals[i],  # Gols da equipe i
                    'score': score
                })
        except Exception as e:
            print(f"Error on page {number_page}: {str(e)}")
    return match_results

match_results = extract_match_results_cbf(1)
print(match_results)

[{'id_match_result': 1, 'id_match': 1, 'local': 'Maracanã - Rio de Janeiro - RJ', 'date': '16/04/2023', 'team': 1, 'name': 'Flamengo - RJ', 'goal': 3, 'score': 3}, {'id_match_result': 2, 'id_match': 1, 'local': 'Maracanã - Rio de Janeiro - RJ', 'date': '16/04/2023', 'team': 2, 'name': 'Flamengo - RJ', 'goal': 0, 'score': 0}]


# Transform and Load
## Encriptify/descriptify and input match results

In [41]:
match_results_encriptify = encryption(match_results)

match_results_descriptify_and_input = decryption_and_loading(match_results_encriptify,'relational.matchs_results','id_match')

[{'id_resultado_jogo': 571, 'id_jogo': 286, 'local': 'Mineirão - Belo Horizonte - MG', '"Data"': '25/10/2023', '"Equipe"': 1, '"Nome"': 'Cruzeiro Saf - MG', '"Gols"': 3, '"Pontos"': 3}, {'id_resultado_jogo': 572, 'id_jogo': 286, 'local': 'Mineirão - Belo Horizonte - MG', '"Data"': '25/10/2023', '"Equipe"': 2, '"Nome"': 'Cruzeiro Saf - MG', '"Gols"': 0, '"Pontos"': 0}]
SELECT id_jogo FROM "Relacional"."Resultados_Jogos";
{1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137